In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg
import os
from tqdm import tqdm
from functools import reduce
import argparse


def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))



DGL backend not selected or invalid.  Assuming PyTorch for now.


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)


In [3]:
dgl_G = dgl.from_networkx(g)

In [4]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
# ramps = [0.02, 0.5]
repeat_num = 1000

In [5]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)

        
    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [6]:
def po_linear_model_square_expo(graph, alpha=1, beta=1, sigma=0.1, gamma=2):    
    for i in graph.nodes:
        graph.nodes[i]["y"] = alpha + beta * graph.nodes[i]["z"] + sigma * np.random.normal() +  gamma * (sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]])/graph.degree[i])**2   

In [ ]:
# cluster-level 



GATE_hat_list = np.zeros((repeat_num, len(ramps)))

     
for seed in tqdm(range(repeat_num)):    
    np.random.seed(seed)     
    rollout_index = np.random.uniform(0, 1, size=(num_cluster,))       
    
    for num_step in range(len(ramps)): 
        print(f"Seed: {seed}")
        torch.manual_seed(2)
        p_list = ramps[num_step:]                            
        g_feat_list = []
        y_list = []
        
        for p in p_list:            
            tr_clusters = np.arange(num_cluster)[rollout_index<np.quantile(rollout_index, p)]            
            tr_units = reduce(lambda x, y: x.union(y), [clusters[i] for i in tr_clusters])  
                        
            nx.set_node_attributes(g, 0, "z")
            nx.set_node_attributes(g, {unit:1 for unit in tr_units}, "z")
            
            po_linear_model_square_expo(g, gamma = 1)            
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN() 
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)        
    
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/Square_expo_CR_cluster.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0
Epoch 0, Treat Prop: 0.02, Loss: 8.1108
Epoch 0, Treat Prop: 0.05, Loss: 2.4082
Epoch 0, Treat Prop: 0.10, Loss: 1.1883
Epoch 0, Treat Prop: 0.25, Loss: 1.5403
Epoch 0, Treat Prop: 0.50, Loss: 3.3474
Epoch 50, Treat Prop: 0.02, Loss: 0.0848
Epoch 50, Treat Prop: 0.05, Loss: 0.1303
Epoch 50, Treat Prop: 0.10, Loss: 0.1183
Epoch 50, Treat Prop: 0.25, Loss: 0.1899
Epoch 50, Treat Prop: 0.50, Loss: 0.7337
Epoch 100, Treat Prop: 0.02, Loss: 0.0358
Epoch 100, Treat Prop: 0.05, Loss: 0.0177
Epoch 100, Treat Prop: 0.10, Loss: 0.0328
Epoch 100, Treat Prop: 0.25, Loss: 0.0442
Epoch 100, Treat Prop: 0.50, Loss: 0.0651
Epoch 150, Treat Prop: 0.02, Loss: 0.0312
Epoch 150, Treat Prop: 0.05, Loss: 0.0149
Epoch 150, Treat Prop: 0.10, Loss: 0.0320
Epoch 150, Treat Prop: 0.25, Loss: 0.0375
Epoch 150, Treat Prop: 0.50, Loss: 0.0557
Epoch 200, Treat Prop: 0.02, Loss: 0.0274
Epoch 200, Treat Prop: 0.05, Loss: 0.0136
Epoch 200, Treat Prop: 0.10, Loss: 0.0309
Epoch 200, Treat Prop: 0.25, Loss: 0.0334

  0%|          | 1/1000 [00:51<14:10:33, 51.08s/it]

0.040293898433446884
Seed: 1
Epoch 0, Treat Prop: 0.02, Loss: 8.1209
Epoch 0, Treat Prop: 0.05, Loss: 2.4594
Epoch 0, Treat Prop: 0.10, Loss: 1.1803
Epoch 0, Treat Prop: 0.25, Loss: 1.7089
Epoch 0, Treat Prop: 0.50, Loss: 3.4916
Epoch 50, Treat Prop: 0.02, Loss: 0.1077
Epoch 50, Treat Prop: 0.05, Loss: 0.1541
Epoch 50, Treat Prop: 0.10, Loss: 0.1228
Epoch 50, Treat Prop: 0.25, Loss: 0.2232
Epoch 50, Treat Prop: 0.50, Loss: 0.7401
Epoch 100, Treat Prop: 0.02, Loss: 0.0297
Epoch 100, Treat Prop: 0.05, Loss: 0.0191
Epoch 100, Treat Prop: 0.10, Loss: 0.0390
Epoch 100, Treat Prop: 0.25, Loss: 0.0440
Epoch 100, Treat Prop: 0.50, Loss: 0.0812
Epoch 150, Treat Prop: 0.02, Loss: 0.0182
Epoch 150, Treat Prop: 0.05, Loss: 0.0177
Epoch 150, Treat Prop: 0.10, Loss: 0.0239
Epoch 150, Treat Prop: 0.25, Loss: 0.0347
Epoch 150, Treat Prop: 0.50, Loss: 0.0639
Epoch 200, Treat Prop: 0.02, Loss: 0.0215
Epoch 200, Treat Prop: 0.05, Loss: 0.0174
Epoch 200, Treat Prop: 0.10, Loss: 0.0303
Epoch 200, Treat Pro

  0%|          | 2/1000 [01:32<12:36:12, 45.46s/it]

...

0.04995601624250412
Seed: 992
Epoch 0, Treat Prop: 0.02, Loss: 8.0863
Epoch 0, Treat Prop: 0.05, Loss: 2.8395
Epoch 0, Treat Prop: 0.10, Loss: 1.5907
Epoch 0, Treat Prop: 0.25, Loss: 1.9296
Epoch 0, Treat Prop: 0.50, Loss: 3.2286
Epoch 50, Treat Prop: 0.02, Loss: 0.0915
Epoch 50, Treat Prop: 0.05, Loss: 0.2176
Epoch 50, Treat Prop: 0.10, Loss: 0.1357
Epoch 50, Treat Prop: 0.25, Loss: 0.1986
Epoch 50, Treat Prop: 0.50, Loss: 0.4674
Epoch 100, Treat Prop: 0.02, Loss: 0.0473
Epoch 100, Treat Prop: 0.05, Loss: 0.0283
Epoch 100, Treat Prop: 0.10, Loss: 0.0462
Epoch 100, Treat Prop: 0.25, Loss: 0.0553
Epoch 100, Treat Prop: 0.50, Loss: 0.0623
Epoch 150, Treat Prop: 0.02, Loss: 0.0381
Epoch 150, Treat Prop: 0.05, Loss: 0.0223
Epoch 150, Treat Prop: 0.10, Loss: 0.0478
Epoch 150, Treat Prop: 0.25, Loss: 0.0453
Epoch 150, Treat Prop: 0.50, Loss: 0.0601
Epoch 200, Treat Prop: 0.02, Loss: 0.0311
Epoch 200, Treat Prop: 0.05, Loss: 0.0218
Epoch 200, Treat Prop: 0.10, Loss: 0.0438
Epoch 200, Treat Pr

 99%|█████████▉| 993/1000 [10:30:20<03:30, 30.02s/it]

0.03887419402599335
Seed: 993
Epoch 0, Treat Prop: 0.02, Loss: 8.0176
Epoch 0, Treat Prop: 0.05, Loss: 2.3849
Epoch 0, Treat Prop: 0.10, Loss: 1.2044
Epoch 0, Treat Prop: 0.25, Loss: 1.8119
Epoch 0, Treat Prop: 0.50, Loss: 3.6849
Epoch 50, Treat Prop: 0.02, Loss: 0.0907
Epoch 50, Treat Prop: 0.05, Loss: 0.1864
Epoch 50, Treat Prop: 0.10, Loss: 0.1453
Epoch 50, Treat Prop: 0.25, Loss: 0.1985
Epoch 50, Treat Prop: 0.50, Loss: 0.6598
Epoch 100, Treat Prop: 0.02, Loss: 0.0327
Epoch 100, Treat Prop: 0.05, Loss: 0.0245
Epoch 100, Treat Prop: 0.10, Loss: 0.0296
Epoch 100, Treat Prop: 0.25, Loss: 0.0577
Epoch 100, Treat Prop: 0.50, Loss: 0.0756
Epoch 150, Treat Prop: 0.02, Loss: 0.0361
Epoch 150, Treat Prop: 0.05, Loss: 0.0178
Epoch 150, Treat Prop: 0.10, Loss: 0.0342
Epoch 150, Treat Prop: 0.25, Loss: 0.0478
Epoch 150, Treat Prop: 0.50, Loss: 0.0659
Epoch 200, Treat Prop: 0.02, Loss: 0.0422
Epoch 200, Treat Prop: 0.05, Loss: 0.0189
Epoch 200, Treat Prop: 0.10, Loss: 0.0331
Epoch 200, Treat Pr

 99%|█████████▉| 994/1000 [10:30:50<02:59, 29.97s/it]

0.05896167829632759
Seed: 994
Epoch 0, Treat Prop: 0.02, Loss: 8.0623
Epoch 0, Treat Prop: 0.05, Loss: 2.4195
Epoch 0, Treat Prop: 0.10, Loss: 1.1645
Epoch 0, Treat Prop: 0.25, Loss: 1.5627
Epoch 0, Treat Prop: 0.50, Loss: 3.1419
Epoch 50, Treat Prop: 0.02, Loss: 0.0683
Epoch 50, Treat Prop: 0.05, Loss: 0.1192
Epoch 50, Treat Prop: 0.10, Loss: 0.0911
Epoch 50, Treat Prop: 0.25, Loss: 0.1621
Epoch 50, Treat Prop: 0.50, Loss: 0.5418
Epoch 100, Treat Prop: 0.02, Loss: 0.0362
Epoch 100, Treat Prop: 0.05, Loss: 0.0200
Epoch 100, Treat Prop: 0.10, Loss: 0.0313
Epoch 100, Treat Prop: 0.25, Loss: 0.0451
Epoch 100, Treat Prop: 0.50, Loss: 0.0576
Epoch 150, Treat Prop: 0.02, Loss: 0.0283
Epoch 150, Treat Prop: 0.05, Loss: 0.0154
Epoch 150, Treat Prop: 0.10, Loss: 0.0292
Epoch 150, Treat Prop: 0.25, Loss: 0.0357
Epoch 150, Treat Prop: 0.50, Loss: 0.0523
Epoch 200, Treat Prop: 0.02, Loss: 0.0261
Epoch 200, Treat Prop: 0.05, Loss: 0.0145
Epoch 200, Treat Prop: 0.10, Loss: 0.0284
Epoch 200, Treat Pr